In [1]:
%matplotlib qt 

import numpy as np
from numpy.random import rand
from landscapeWithOcean import LandscapeWithOcean # Import methods from inside file landscapeWithOcean.py

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm

In [2]:
def AddHill(Z,NX,NY,xx,yy,r,h):

    for x in range(NX):
        for y in range(NY):
            dx = np.mod(x-xx+NX/2,NX)-NX/2;  #times -1/ i switched all the signs. 
            dy = np.mod(y-yy+NY/2,NY)-NY/2; #times -1/ i switched all the signs
            dr = np.sqrt(dx**2+dy**2);
            if (dr<r):
                Z[x,y] += h * (np.cos(dr/r*np.pi/2.0))**2;

    return Z

In [73]:
NX = 100 #number of rows #originally 40 #45 #60
NY = 100 #number of columns #40 #45 #60

#increasing NX and NY increases the elevation even if you keep all the other values constant

d  = 5 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d

LX=NX*dx
LY=NY*dy

# small random features in topography to begin erosion

#make an array of 1's and append from there 
z = np.ones((NX,NY)) #or np.ones/zeros
##to create bowl shape

"CIRCULAR HILL"
for i in range(NX):
    for j in range(NY):
        xx = i 
        yy = j 
        r = 30
        h = 120 #100
        if xx==0 or yy==0:
            Z = AddHill(z,NX,NY,xx,yy,r,h)
'BRYCE CANYON'           
##a bunch of hills/ beads
for i in range(NX):
    xx = i
    yy = i**3
    r  = 6.7 # 3
    h  = 24.03*i #8.03*i
    if 25<yy<75 or 25<xx<75:
        Z = AddHill(z,NX,NY,xx,yy,r,h)

for i in range(25,50):
    xx = i*i
    yy = i**3 #3 for nose, 1 for other one
    r  = 4.6 #4
    h  = 29.65*i #6.65*i
    Z = AddHill(z,NX,NY,xx,yy,r,h)

        
plt.imshow(Z)
    
x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) #strange that y goes first !!!
ZMaxOrg = np.max(Z)
#print(ZMaxOrg)

In [74]:
### Physical Parameters
K = 2.5e-19 # meters^(1-2m)/yr  ##1.0e-6 #2.5e-9

D = 1.75 # m^2/yr #0.005

# uplift rate
# uplift = 0.03 / 600.
uplift = 60.01 #0.01

In [75]:
### Model parameters

# Time step
#dt = d**2 / D / 8. 
dt = d**2 / D /16. #extra small steps 
print(' dt[years] = ',dt)

#Area exponent A^m, default m=1
m=2

#gradient exponent g^n, default n=1
n=2/3

#erosion threshold 
theta_c = 10 #10  

 dt[years] =  0.8928571428571429


In [76]:
# Total simulation time
T = 1.0 * 625.0 # 1000.0 * 625.0

# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of interation: ',n_iter)

Number of interation:  700


In [77]:
# Initialize landscape 
ls = LandscapeWithOcean(NX,NY)

oceanLevelParameter=0.001 #was 0.1 # what does this parameter do? #i had it at .01
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

Minimum elevation           1.0
Maximum elevation           9156.5
Beach level                 10.1555
Ocean volume                4215.134643946379
Percentage of ocean surface 5.37


In [80]:
# Set-up figure

#from matplotlib.animation import FFMpegWriter
#metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
#writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
#fig = plt.figure(dpi=200)

def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure():
        plt.clf()
        ax1 = fig.add_subplot(121,projection='3d')

        # use equal x-y aspect with an explicit vertical exageration
        vert_exag = 4.
        ax1.set_xlim3d(0,max(NX,NY))
        ax1.set_ylim3d(0,max(NX,NY))
        ax1.set_zlim3d(0,ZMaxOrg)

        ax1.set_title('Surface Relief')

#        surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
#                antialiased=False,linewidth=0)

        ZPlot = np.copy(Z)
        ZPlot[ZPlot<ls.ZBeachLevel] = ls.ZBeachLevel 
        ZPlot -= ls.ZBeachLevel
        ax1.view_init(60+5*np.exp(-it/50), -15+(45*it/100))
        ax1.plot_surface(X,Y,ZPlot, cmap = cm.Spectral, rstride=1, cstride=1,
                antialiased=False,linewidth=0)

        ax2 = fig.add_subplot(122,aspect='equal')
        ax2.set_title('Elevation')

        #im = ax2.pcolor(Z,cmap=cm.terrain)
        im = ax2.pcolor(ZPlot,cmap=cm.Spectral)
        cs = ax2.contour(ZPlot,6,colors='k')

        # Add a color bar which maps values to colors.
        cbar = fig.colorbar(im, shrink=0.5, aspect=5)
        # Add the contour line levels to the colorbar
        cbar.add_lines(cs)

        #plt.show()
        plt.draw()
        plt.pause(0.0001)

In [81]:
# Set up figure
from matplotlib.animation import FFMpegWriter
#metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
#writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
#fig = plt.figure(dpi=200)

plt.rcParams['animation.ffmpeg_path']='C:\\Users\\olivi\\Downloads\\ffmpeg.exe'
#plt.rcParams['animation.ffmpeg_path']='C:\\Users\\olivi\\Downloads\\ffmpeg-20191013-4f4334b-win64-static\\ffmpeg-20191013-4f4334b-win64-static\\bin\\ffmpeg.exe'
metadata = dict(title='My first animation in 2D', artist='Matplotlib',comment='Wakanda is coming.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
#fig = plt.figure(dpi=200)

fig = init_figure()
update_figure()
Znew = np.copy(Z)
with writer.saving(fig, "wave2dC.mp4", dpi =200):


    for it in range(1,n_iter+1):

        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy

        for i in range(NX):
            iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
            iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: #this cell is a drain
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                    elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02 # ??? This does happen (maybe when two pools merge)
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                    else: #this cell is a pool, assume it has some mass diffusion but no erosion!
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    # diffusion term
                    Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                #if (CFL>1.0):
                    #print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero

        #Znew[0,:] = 0.0 # resets front boundary to 0
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)

        if (np.mod(it,10)==0): 
            print(it,end='')
            update_figure()
            print(' Ocean level=',ls.ZBeachLevel, ' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
        else:
            print('.',end='')
            
    
        plt.pause(0.01)
        writer.grab_frame()

update_figure()
print(' Simulation finished.')


.........10 Ocean level= 599.854672543045  Ocean surface fraction= 5.38
.........20 Ocean level= 1135.6582439716162  Ocean surface fraction= 5.38
.........30 Ocean level= 1671.4618154001873  Ocean surface fraction= 5.38
.........40 Ocean level= 2207.265386828759  Ocean surface fraction= 5.38
.........50 Ocean level= 2743.0689582573323  Ocean surface fraction= 5.38
.........60 Ocean level= 3278.8725296859056  Ocean surface fraction= 5.38
.........70 Ocean level= 3814.676101114479  Ocean surface fraction= 5.38
.........80 Ocean level= 4350.479672543051  Ocean surface fraction= 5.38
.........90 Ocean level= 4886.283243971619  Ocean surface fraction= 5.38
.........100 Ocean level= 5422.086815400188  Ocean surface fraction= 5.38
.........110 Ocean level= 5957.890386828757  Ocean surface fraction= 5.38
.........120 Ocean level= 6493.693958257326  Ocean surface fraction= 5.38
.........130 Ocean level= 7029.497529685895  Ocean surface fraction= 5.38
.........140 Ocean level= 7565.301101114464 